In [2]:
import paramiko
import pandas as pd
from datetime import datetime
import time


def get_data(hostname, port, username, password, script_path):
    try:
        client = paramiko.SSHClient()
        client.set_missing_host_key_policy(paramiko.AutoAddPolicy())
        client.connect(hostname, port, username, password)

        stdin, stdout, stderr = client.exec_command(f'python3 {script_path}')
        output = stdout.read().decode('utf-8').strip()

        client.close()

        output_pairs = output.split(',')

        variable_values = [float(pair.split('=')[1]) for pair in output_pairs]

        variable1, variable2, variable3 = variable_values

        return variable1, variable2, variable3

    except Exception as e:
        print(f"An error occurred: {e}")
        return None, None, None


df = pd.read_csv('Data.csv')
while True:
    try:
        temp, pressure, humidity = get_data('192.168.1.123', 22, 'hoehenmichae', 'pi',
                                            '/home/hoehenmichae/Documents/project/code.py')
        time_1 = datetime.now().time().replace(microsecond=0)
        date_1 = datetime.today().date().strftime('%d-%m-%Y')
        df_temp = pd.DataFrame(
            {'Date': [date_1], 'Time': [time_1], 'Temperature': [temp], 'Barometric Pressure': [pressure],
             'Humidity': [humidity]})
        df = pd.concat([df, df_temp])
        df.to_csv('Data.csv', index=False)
        time.sleep(59)

    except KeyboardInterrupt:
        break

df.to_csv('Data.csv', index=False)
df

Date      Time  Temperature  Barometric Pressure  Humidity
0   23-12-2023  10:31:44         9.14               962.54    61.900
1   23-12-2023  10:33:26         9.19               962.56    62.583
2   23-12-2023  10:34:26         9.14               962.59    61.835
3   23-12-2023  10:35:26         8.95               962.61    62.270
4   23-12-2023  10:36:26         8.91               962.67    61.414
..         ...       ...          ...                  ...       ...
0   15-01-2024  17:16:34         1.18               951.71    79.291
0   15-01-2024  17:17:34         1.19               951.74    78.544
0   15-01-2024  17:18:34         1.22               951.72    78.812
0   15-01-2024  17:19:33         1.23               951.74    79.127
0   15-01-2024  17:20:33         1.23               951.65    78.431

[530 rows x 5 columns]